In [21]:
# Load libraries
import pandas
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn import tree
import random
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.preprocessing import StandardScaler
import shap
import xgboost as xgb
import re
from scipy import stats
import pickle
import os
seed = 0
deterministic = True

random.seed(seed)
np.random.seed(seed)
with open('folk_employment_df.pickle', 'rb') as f:
    dataframe = pickle.load(f)
with open('folk_employment_label.pickle', 'rb') as f:
    labels = pickle.load(f)
dataframe['US Born']=dataframe['US Born'].replace(1,0)
dataframe['US Born']=dataframe['US Born'].replace(2,1)
dataframe['US Born']    
ordinal = ['Age','Education']
for c in ordinal:
    dataframe[c] = dataframe[c].astype(int)
D = 5
FEAT_NUM = dataframe.shape[1]
PERCENT = 75

In [2]:
dataframe.describe()

Age      Education        US Born  Hearing Difficulty   
count  359931.000000  359931.000000  359931.000000       359931.000000  \
mean       42.380801      16.342874       0.273336            1.963132   
std        22.052769       5.612494       0.445672            0.188438   
min         5.000000       1.000000       0.000000            1.000000   
25%        24.000000      14.000000       0.000000            2.000000   
50%        42.000000      18.000000       0.000000            2.000000   
75%        60.000000      21.000000       1.000000            2.000000   
max        94.000000      24.000000       1.000000            2.000000   

       Vision Difficulty  Cognitive Difficulty       Divorced        Married   
count      359931.000000         359931.000000  359931.000000  359931.000000  \
mean            0.023241              0.051688       0.082335       0.431155   
std             0.150667              0.221396       0.274875       0.495238   
min             0.000000              0.000000       0.000000       0.000000   
25%             0.000000              0.000000       0.000000       0.000000   
50%             0.000000              0.000000       0.000000       0.000000   
75%             0.000000              0.000000       0.000000       1.000000   
max             1.000000              1.000000       1.000000       1.000000   

       Never married or under 15 years old      Separated  ...           Male   
count                        359931.000000  359931.000000  ...  359931.000000  \
mean                              0.423087       0.015753  ...       0.492097   
std                               0.494050       0.124519  ...       0.499938   
min                               0.000000       0.000000  ...       0.000000   
25%                               0.000000       0.000000  ...       0.000000   
50%                               0.000000       0.000000  ...       0.000000   
75%                               1.000000       0.000000  ...       1.000000   
max                               1.000000       1.000000  ...       1.000000   

       Alaska Native alone  American Indian alone   
count        359931.000000          359931.000000  \
mean              0.000075               0.007443   
std               0.008661               0.085952   
min               0.000000               0.000000   
25%               0.000000               0.000000   
50%               0.000000               0.000000   
75%               0.000000               0.000000   
max               1.000000               1.000000   

       American Indian and Alaska Native tribes specified;or American Indian or Alaska Native,not specified and no other   
count                                      359931.000000                                                                  \
mean                                            0.002353                                                                   
std                                             0.048453                                                                   
min                                             0.000000                                                                   
25%                                             0.000000                                                                   
50%                                             0.000000                                                                   
75%                                             0.000000                                                                   
max                                             1.000000                                                                   

         Asian alone  Black or African American alone   
count  359931.000000                    359931.000000  \
mean        0.158769                         0.048648   
std         0.365461                         0.215132   
min         0.000000                         0.000000   
25%         0.00000

In [3]:
### Slicing data ###
X = dataframe.values
X = np.array(X,dtype='float64')
y = labels.values
# Split train/test by 8:2. msk refers to the indices of the training data. Will be used for indexing Concepts
df = pandas.DataFrame(np.random.randn(dataframe.shape[0], 2))
msk = np.random.rand(len(df)) < 0.8
train_data = dataframe[msk]
test_data = dataframe[~msk]
X_train, y_train = X[msk], y[msk]
X_test, y_test = X[~msk], y[~msk]
#Save original training data for computing values
X_train_og =  dataframe.iloc[msk]
y_train_og =  y[msk]


# Decision Tree performance

In [4]:
dt = DecisionTreeClassifier(criterion = "gini",
                               max_depth=5, min_samples_leaf=5)
dt.fit(X_train, y_train)
y_pred_dt = dt.predict(X_test)
print(f"Decision Tree using Gini Index\nAccuracy is {accuracy_score(y_test,y_pred_dt)*100} f1 {f1_score(y_test,y_pred_dt)*100}","\n\nPrecision Value is\n", classification_report(y_test,y_pred_dt))

Decision Tree using Gini Index
Accuracy is 78.62867938157218 f1 79.2299488342581 

Precision Value is
               precision    recall  f1-score   support

         0.0       0.84      0.73      0.78     37471
         1.0       0.74      0.85      0.79     34518

    accuracy                           0.79     71989
   macro avg       0.79      0.79      0.79     71989
weighted avg       0.79      0.79      0.79     71989



In [5]:
### Desicion Tree with Gini Index ###

dt_clf_gini = RandomForestClassifier(criterion = "gini",
                               max_depth=6, min_samples_leaf=5,n_estimators=5)
dt_clf_gini.fit(X_train, y_train)

RandomForestClassifier(max_depth=6, min_samples_leaf=5, n_estimators=5)

 #### Now Predicting data on both classifiers using the test values

In [6]:
### Desicion Tree with Gini Index ###

dt_clf_gini = RandomForestClassifier(criterion = "gini",
                               max_depth=5, min_samples_leaf=5,n_estimators=5)
dt_clf_gini.fit(X_train, y_train)
y_pred_gini = dt_clf_gini.predict(X_test)
print(f"Decision Tree using Gini Index\nAccuracy is {accuracy_score(y_test,y_pred_gini)*100} f1 {f1_score(y_test,y_pred_gini)*100}","\n\nPrecision Value is\n", classification_report(y_test,y_pred_gini))

Decision Tree using Gini Index
Accuracy is 77.73687646723805 f1 78.98236181234019 

Precision Value is
               precision    recall  f1-score   support

         0.0       0.85      0.69      0.76     37471
         1.0       0.72      0.87      0.79     34518

    accuracy                           0.78     71989
   macro avg       0.79      0.78      0.78     71989
weighted avg       0.79      0.78      0.78     71989



#### --> Accuracy Scores And Precision value

In [7]:
# explainer = shap.TreeExplainer(dt_clf_gini, X_train)
# shap_values = explainer.shap_values(X_train)

In [8]:
rf_explainer = shap.TreeExplainer(dt_clf_gini, X_train)
rf_shap_values = rf_explainer.shap_values(X_train)
plt.rcParams['axes.unicode_minus'] = False
plt.tight_layout()
shap.summary_plot(rf_shap_values[1], X_train,
                  feature_names=dataframe.columns, 
                 cmap='bwr', show=False,max_display=1000,sort=True)
plt.xlabel('SHAP Value')
plt.title('Employed', fontsize=20)
plt.show()
plt.savefig('shap/ACS_eemployment_rf.png',bbox_inches='tight')

 99%|===================| 567358/575884 [01:04<00:00]        No data for colormapping provided via 'c'. Parameters 'vmin', 'vmax' will be ignored
Tight layout not applied. The left and right margins cannot be made large enough to accommodate all axes decorations.


# Concept Extraction

In [9]:
# find path to the node by its node_numb
def find_path(node_numb, path, x):
        path.append(node_numb)
        if node_numb == x:
            return True
        left = False
        right = False
        if (children_left[node_numb] !=-1):
            left = find_path(children_left[node_numb], path, x)
        if (children_right[node_numb] !=-1):
            right = find_path(children_right[node_numb], path, x)
        if left or right :
            return True
        path.remove(node_numb)
        return False

# Given path information, get the rule
def get_rule(path, column_names):
    mask = ''
    for index, node in enumerate(path):
        #We check if we are not in the leaf
        if index!=len(path)-1:
            # Do we go under or over the threshold ?
            if (children_left[node] == path[index+1]):
                mask += f"(dataframe['{column_names[feature[node]]}']<= {threshold[node]}) \t "
            else:
                mask += f"(dataframe['{column_names[feature[node]]}']> {threshold[node]}) \t "
    # We insert the & at the right places
    mask = mask.replace("\t", "&", mask.count("\t") - 1)
    mask = mask.replace("\t", "")
    return mask

# compute node entropy
def gini(a):
    p1 = float(sum(a)/len(a))
    p2 = float((len(a)-sum(a))/len(a))
    return 1-p1**2-p2**2

# Compute the gini index, support of the rule, proprtion wrt to the support, depth of the tree
def compute_gini_size(rule):
    rule = rule.replace("dataframe","X_train_og")
    depth = rule.count('&') +1
    concept = 'c1 = '+rule
    exec(concept,globals())
    x = y_train_og[c1]
    return 1-gini(x), len(x), float(sum(x))/len(x)*100, depth 

# Concept Extraction

In [10]:
rules = set() #set of rules
rule_entropy_dict = dict() # entropy for each rule
rule_depth = dict() # depth for each rule
rule_sample_num = dict() # sample number per rule
rule_pos_neg = dict() # The percentage of positive label wrt to the support 

#iterate each tree
for tree in dt_clf_gini.estimators_:
    n_nodes = tree.tree_.node_count
    children_left = tree.tree_.children_left
    children_right = tree.tree_.children_right
    feature = tree.tree_.feature
    threshold = tree.tree_.threshold
    
    # compute if leaf
    node_depth = np.zeros(shape=n_nodes, dtype=np.int64)
    is_leaves = np.zeros(shape=n_nodes, dtype=bool)
    stack = [(0, 0)]  # start with the root node id (0) and its depth (0)
    while len(stack) > 0:
        # `pop` ensures each node is only visited once
        node_id, depth = stack.pop()
        node_depth[node_id] = depth
        #n_node_samples[i]
        # If the left and right child of a node is not the same we have a split
        # node
        is_split_node = children_left[node_id] != children_right[node_id]
        # If a split node, append left and right children and depth to `stack`
        # so we can loop through them
        if is_split_node:
            stack.append((children_left[node_id], depth + 1))
            stack.append((children_right[node_id], depth + 1))
        else:
            is_leaves[node_id] = True
    l = list()
    for node in range(1,n_nodes):
        if node_depth[node] <= D:
            l.append(node)
    paths ={}
    for node in np.unique(l):
        path = []
        find_path(0, path, node)
        paths[node] = np.unique(np.sort(path))
        rule = get_rule(paths[node], dataframe.columns)
        rules.add(rule)
        if not rule in rule_entropy_dict: 
            impurity,sample_size,percent,depth = compute_gini_size(rule)
            rule_entropy_dict[rule] = impurity
            rule_depth[rule] = depth
            rule_sample_num[rule] = sample_size
            rule_pos_neg[rule] = percent
rules = sorted(rules)


In [11]:
# Sort the rules by impurity
rule_entropy_dict = {k: v for k, v in sorted(rule_entropy_dict.items(), key=lambda item: item[1],reverse=True)}
#Compute the percentage of the rules
TOPK = int(len(rules) * PERCENT*0.01)
score_dict = dict()
for rule in rules:
    score_dict[rule] = rule_entropy_dict[rule]*rule_sample_num[rule]
# Extract top k% of the rules by score
rules = list(score_dict.keys())[:TOPK]
print(f'Number of rules extracted {len(rules)}')

Number of rules extracted 196


## Convert Rules to explanations

In [12]:
explanations = []
ordinal = ['Age','Education']
for i in range(len(rules)):
    rule = rules[i]
    posneg = rule_pos_neg[rule]
    score = score_dict[rule]
    features = re.findall("'([^']*)'", rule)
    thresholds = re.findall("\d+\.\d+", rule)
    rule = rule.replace("dataframe","X_train_og")
    command = 'c1 = '+rule
    exec(command)
    group = X_train_og[c1]
    total_percentage = (len(group)/len(dataframe)*100)
    explanation = f'Population: {total_percentage:.1f}% positive:{posneg:.1f}% score: {score/max(score_dict.values()):.1f}'
    r = rule.split('&')
    for j,f in enumerate(r):
        command = f'c1 = {f}'
        exec(command)
        group = X_train_og[c1]
        if features[j] in ordinal:
            #Given a threshold, compute the percentile of the feature value belongs to.
            # Ex) education > 12: 10 means that 10% of the data points have education > 12
            # Ex2) education <=12: 90 means that 90% of the data points have education <=12 
            percentile = stats.percentileofscore(X_train_og[features[j]], float(thresholds[j]),'weak')
            if '>' in f:
                percentile = 100-percentile
                explanation += f' ({features[j]}>{float(thresholds[j]):.1f}: P_{percentile:.1f})'
            else:
                explanation += f' ({features[j]}<={float(thresholds[j]):.1f}: P_{percentile:.1f})'
            
        else:
            percentage = len(group)/len(dataframe)*100
            if '>' in f:
                explanation += f' ({features[j]} True: {percentage:.1f}%)'
            else:
                explanation += f' ({features[j]} False: {percentage:.1f}%)'
    explanations.append(explanation)


In [13]:
# For each row, create a new input for the Concept Network.
## if the row belongs to a concept, it is labelled 1 and 0 otherwise.
cur_len = len(rules)
concepts = list()
for rule in rules:
    concept = 'c1 = '+rule
    exec(concept)
    c1 = c1.astype(float)
    c1 = list(c1)
    concepts.append(c1)        
l = list()
for i in range(len(concepts[0])):
    tmp = list()
    for c in concepts:
        tmp.append(c[i])
    l.append(tmp)
l = [tuple(i) for i in l]
l_train_og = [l[i] for i,v in enumerate(msk) if v]

# Base XGBoost

In [14]:
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test= sc.fit_transform(X_test)
base_model=xgb.XGBClassifier()
base_model.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [15]:
preds = base_model.predict(X_test)
print(f'acc: {accuracy_score(preds,y_test)} f1: {f1_score(preds,y_test)}')

acc: 0.8015391240328383 f1: 0.8053409632808773


In [16]:
# Sort False
base_explainer = shap.TreeExplainer(base_model, X_train)
base_shap_values = base_explainer.shap_values(X_train)
print(base_shap_values.shape)
plt.rcParams['axes.unicode_minus'] = False
plt.tight_layout()
shap.summary_plot(base_shap_values, X_train,
                  feature_names=dataframe.columns, 
                 cmap='bwr', show=False,max_display=len(dataframe.columns),sort=False)
plt.xlabel('SHAP Value')
plt.title('Employed', fontsize=20)
plt.show()
plt.savefig('shap/ACS_eemployment_base.png',bbox_inches='tight')

100%|===================| 287788/287942 [15:24<00:00]        

(287942, 44)


No data for colormapping provided via 'c'. Parameters 'vmin', 'vmax' will be ignored
Tight layout not applied. The left and right margins cannot be made large enough to accommodate all axes decorations.


# C>Y


In [17]:
C_train, y_train =  [l[i] for i,v in enumerate(msk) if v], y[msk]
C_test, y_test = [l[i] for i,v in enumerate(msk) if not v], y[~msk]

sc = StandardScaler()
C_train = sc.fit_transform(C_train)
C_test= sc.fit_transform(C_test)
concept_model=xgb.XGBClassifier()
concept_model.fit(C_train,y_train)

preds = concept_model.predict(C_train)

In [18]:
preds = concept_model.predict(C_test)
print(f'acc: {accuracy_score(preds,y_test)} f1: {f1_score(preds,y_test)}')
print(f'prec {precision_score(preds,y_test)} recall {recall_score(preds,y_test)}')

acc: 0.7918987623109086 f1: 0.8001600747015273
prec 0.8688800046352627 recall 0.7415135856800257


In [19]:
c_explainer = shap.TreeExplainer(concept_model, C_train)
c_shap_values = c_explainer.shap_values(C_train)

100%|===================| 287819/287942 [06:57<00:00]        

In [22]:
if not os.path.exists("shap"):
    os.makedirs("shap")
plt.tight_layout()
plt.rcParams['axes.unicode_minus'] = False
shap.summary_plot(c_shap_values, C_train,
                  feature_names=explanations, 
                 cmap='bwr', show=False,max_display=len(rules),sort=False)
plt.xlabel('SHAP Value')
plt.title('Earn >50k', fontsize=20)
plt.show()
plt.savefig('shap/ACS_employment.png',bbox_inches='tight')

No data for colormapping provided via 'c'. Parameters 'vmin', 'vmax' will be ignored
Tight layout not applied. The left and right margins cannot be made large enough to accommodate all axes decorations.


<Figure size 640x480 with 0 Axes>

In [23]:
pred_base = base_model.predict(X_train)
pred_c = concept_model.predict(C_train)
agreed = [pred_base[i] == pred_c[i] for i in range(len(pred_base))]
print(f'train {sum(agreed)/len(agreed)*100:.2f} agreed')

train 93.86 agreed


In [24]:
cur_depth = 1
for rule in sorted(rules):
    out = f'{rule}\n entropy: {1-rule_entropy_dict[rule]:.3f}, 50k Ratio: {rule_pos_neg[rule]:.2f}%, sample size: {rule_sample_num[rule]}\n'
    depth = rule_depth[rule]
    if depth != cur_depth:
        if depth <cur_depth:
            print('*************NEW TREE*****************')
        cur_depth = depth
        out+='\n'
    print(out)

(dataframe['Born in the U.S']<= 0.5)  
 entropy: 0.493, 50k Ratio: 56.06%, sample size: 82749

(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5)  
 entropy: 0.447, 50k Ratio: 66.27%, sample size: 65734


(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']<= 0.5)  
 entropy: 0.296, 50k Ratio: 18.04%, sample size: 4168


(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']<= 0.5) & (dataframe['Married']<= 0.5)  
 entropy: 0.144, 50k Ratio: 7.83%, sample size: 3474


(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']<= 0.5) & (dataframe['Married']<= 0.5) & (dataframe['Received military training']<= 0.5)  
 entropy: 0.128, 50k Ratio: 6.85%, sample size: 3414


(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']<= 0.5) & (dataframe['Married']<= 0.5

In [25]:
for rule in {k: v for k, v in sorted(score_dict.items(), key=lambda item: item[1],reverse=True)}:
    out = f'{rule}\n entropy: {1-rule_entropy_dict[rule]:.3f}, 50k Ratio: {rule_pos_neg[rule]:.2f}%, sample size: {rule_sample_num[rule]}\n'
    depth = rule_depth[rule]
    if depth != cur_depth:
        if depth <cur_depth:
            print('*************NEW TREE*****************')
        cur_depth = depth
        out+='\n'
    print(out)

(dataframe['Living with two parents: both parents in labor force']<= 0.5)  
 entropy: 0.500, 50k Ratio: 51.26%, sample size: 269097

(dataframe['Living with two parents: both parents in labor force']<= 0.5) & (dataframe['DIS_Without a disability']> 0.5)  
 entropy: 0.491, 50k Ratio: 56.55%, sample size: 232466


*************NEW TREE*****************
(dataframe['Never served in the military']> 0.5)  
 entropy: 0.488, 50k Ratio: 57.89%, sample size: 227915


(dataframe['Never served in the military']> 0.5) & (dataframe['Widowed']<= 0.5)  
 entropy: 0.479, 50k Ratio: 60.24%, sample size: 215482


*************NEW TREE*****************
(dataframe['Education']> 14.5)  
 entropy: 0.483, 50k Ratio: 59.09%, sample size: 213503


(dataframe['Living with two parents: both parents in labor force']<= 0.5) & (dataframe['DIS_Without a disability']> 0.5) & (dataframe['Age']> 18.5)  
 entropy: 0.459, 50k Ratio: 64.38%, sample size: 201670


(dataframe['Never served in the military']> 0.5) & (datafram

In [26]:
for rule in {k: v for k, v in sorted(rule_pos_neg.items(), key=lambda item: item[1],reverse=True)}:
    out = f'{rule}, D:{rule_depth[rule]}\n entropy: {rule_entropy_dict[rule]:.3f}, pos:neg {rule_pos_neg[rule]:.2f}, sample size: {rule_sample_num[rule]}\n'
    depth = rule_depth[rule]
    if depth != cur_depth:
        if depth <cur_depth:
            print('*************NEW TREE*****************')
        cur_depth = depth
        out+='\n'
    print(out)

(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']> 0.5) & (dataframe['Education']> 19.5) & (dataframe['Lived in different house in US or Puerto Rico']<= 0.5)  , D:5
 entropy: 0.650, pos:neg 77.35, sample size: 20977

*************NEW TREE*****************
(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']> 0.5) & (dataframe['Education']> 19.5)  , D:4
 entropy: 0.649, pos:neg 77.29, sample size: 23954


(dataframe['Born in the U.S']<= 0.5) & (dataframe['Age']<= 64.5) & (dataframe['Never served in the military']> 0.5) & (dataframe['Education']> 19.5) & (dataframe['Lived in different house in US or Puerto Rico']> 0.5)  , D:5
 entropy: 0.644, pos:neg 76.82, sample size: 2977


(dataframe['Living with two parents: both parents in labor force']<= 0.5) & (dataframe['DIS_Without a disability']> 0.5) & (dataframe['Age']> 18.5) & (dataframe['Some Other Race alone']> 0.5) & (data